In [1]:
import numpy as np
import pickle
#MPLD3 lets us make an html of a matplotlib plot:
import matplotlib.pyplot as plt, mpld3
import seaborn as sns
import pandas as pd
#Mapping Specific imports:
import json 
import requests
from shapely.geometry import shape, Point
import folium

In [2]:
df = pd.read_csv('./data/cluster_student_counts.csv')
school_df = pd.read_csv('./data/school_df_v1.csv')

#URL for neighborhood boundaries:
neighbs_url = 'https://opendata.arcgis.com/datasets/f6c703ebe2534fc3800609a07bad8f5b_17.geojson'

#URL for the DC area boundary:
dc_area_url = 'https://opendata.arcgis.com/datasets/7241f6d500b44288ad983f0942b39663_10.geojson'

#URL for Wards:
ward_url = 'https://opendata.arcgis.com/datasets/0ef47379cbae44e88267c01eaec2ff6e_31.geojson'

#Reading in the neighborhood data
resp = requests.get(neighbs_url)
neighbs_data = resp.json()

#Reading in the ward data
resp2 = requests.get(ward_url)
ward_data = resp2.json()

school_df['neighborhood'] = np.nan


##Setting the neighborhood for each school using shapely:

for neb in range(len(neighbs_data['features'])): #len(neighbs_data['features'])
  
  outline = shape(neighbs_data['features'][neb]['geometry'])
  #print(neb)
  #neighbs_data['features'][neb]['geometry'] should give us the geometry of the neighborhood. Next we need to check
  #if the school is inside that geometry:
  for school in range(len(school_df)):

    location = Point(school_df['school_longitude'].iloc[school], school_df['school_latitude'].iloc[school])
    name = school_df.iloc[school]['school_name']
    if outline.contains(location):
      #Uncomment below if you want a full printout of the loop finding the neighborhood:
      #print(f'School #{name} is in neighborhood {neb} ')
      #print('----')
      #print(school_data.iloc[school])
        school_df.iloc[school, school_df.columns.get_loc('neighborhood')] = neb
        pass
    else:
        pass
    
#### END MAPPING SETUP ####

In [5]:
df.columns

Index(['Neighborhood Cluster', 'Neighborhood Cluster Names', 'School Year_x',
       'Count of English Learner Students',
       'English Learner Students as  share of Neighborhood Cluster',
       'Count of At Risk Students', 'At Risk as share of Neighborhood Cluster',
       'Count of Special Education Students',
       'Special Education Students as share of Neighborhood Cluster',
       'Sum of Enrollment by Sector and Grade Band',
       'Sum of Total Enrollment (DCPS & PCS)'],
      dtype='object')

In [9]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 75 entries, 0 to 74
Data columns (total 11 columns):
 #   Column                                                       Non-Null Count  Dtype  
---  ------                                                       --------------  -----  
 0   Neighborhood Cluster                                         75 non-null     object 
 1   Neighborhood Cluster Names                                   75 non-null     object 
 2   School Year_x                                                75 non-null     object 
 3   Count of English Learner Students                            75 non-null     object 
 4   English Learner Students as  share of Neighborhood Cluster   75 non-null     object 
 5   Count of At Risk Students                                    75 non-null     int64  
 6   At Risk as share of Neighborhood Cluster                     75 non-null     float64
 7   Count of Special Education Students                          75 non-null     objec

In [11]:
var_1 = 'Count of At Risk Students'
var_2 = 'Sum of Enrollment by Sector and Grade Band'

In [13]:
#Defining our Map:
m2 = folium.Map(location = [38.9, -77], zoom_start=10.5)
#Adding a neighborhood layer:
neighborhood_layer = folium.FeatureGroup(name='Neighborhoods', show=False, )
#folium.GeoJson(test_dict).add_to(neighborhood_layer)
folium.Choropleth(
    geo_data = neighbs_url,
    data = df,
    columns = ['Neighborhood Cluster', var_1],
    key_on='feature.properties.NAME',
    fill_color='Oranges',
    fill_opacity = .6,
    name = var_1
).add_to(m2)
folium.Choropleth(
    geo_data = neighbs_url,
    data = df,
    columns = ['Neighborhood Cluster',var_2],
    key_on='feature.properties.NAME',
    fill_color='YlGnBu',
    fill_opacity = .6,
    name = var_2
).add_to(m2)
#neighborhood_layer.add_to(m)

folium.LayerControl().add_to(m2)
#Display the map:
m2